In [5]:
from pytube import YouTube
from moviepy.editor import AudioFileClip
import IPython.display as ipd
from openai import AzureOpenAI
import os

# Use Azure OpenAI API
client = AzureOpenAI(
    azure_endpoint = os.getenv("AZURE_OPENAI_ENDPOINT"),
    api_version = os.getenv("AZURE_OPENAI_API_VERSION"),
    api_key = os.getenv("AZURE_OPENAI_API_KEY")
)

url = input("Enter the URL of the YouTube video you want to download: ")

youtube = YouTube(url)

def download_audio(youtube):
    audio_stream = youtube.streams.filter(only_audio=True).first()
    filename = audio_stream.default_filename
    download_path = os.path.join('yt', filename)
    audio_stream.download(filename=download_path)

    # Convert to mp3
    clip = AudioFileClip(download_path)
    mp3_filename = filename.rsplit(".", 1)[0] + ".mp3"
    mp3_path = os.path.join('yt', mp3_filename)
    clip.write_audiofile(mp3_path)
    
    return mp3_path

mp3_path = download_audio(youtube)

# Open file in local directory in the data folder called 'trimmed_EarningsCall.wav
audio_file= open(mp3_path, "rb")

# Transcribe the audio file
transcript = client.audio.transcriptions.create(
    model="whisper", 
    file=audio_file
)

# Print the transcript
print(transcript.text)

# Save transcript to as a text file
with open('yt/transcript.txt', 'w') as f:
    f.write(transcript.text)

txt = transcript.text

# Play the audio
ipd.Audio(mp3_path)

MoviePy - Writing audio in yt\Chest Pain.mp3


MoviePy - Done.
This one they just handed me the EKG from triage and it looks like they're having a heart attack. Hi there I'm Dr. Beggars, this is Jake my assistant. What it looks like on your EKG you might be having a heart attack so we're going to be doing a lot of stuff really quickly but we're going to have to get you to the cath lab. Nurse can you go ahead and give me an IV O2 monitor let's get a cardiac workup triage protocol. We're going to need a CBC, a BMP, a troponin, a chest x-ray. Have you had any recent bleeding or clotting disorders any history of GI bleed or anything like that? Okay so we'll go ahead and get a heparin bolus, heparin drip that's going to be the MI protocol for that and a nitro drip going as well and some aspirin for baby aspirin. Can you tell me when your symptoms started? About a couple hours ago it started out off and on for a little bit it started right here all the way up my neck and into my arm but it was a short it started out just you know off and

In [2]:
# Define function to add punctuation
def punctuation_assistant(txt):
    response = client.chat.completions.create(
        model="gpt-35-turbo",
        temperature=0,
        messages=[
            {
                "role": "system", 
                "content": "You are a helpful assistant that adds punctuation to text. Preserve the original words and only insert necessary punctuation such as periods, commas, capialization, symbols like dollar sings or percentage signs, and formatting. Use only the context provided."
            },
            {
                "role": "user", 
                "content": txt  
            }
        ]
    )

    punctuated_txt = response.choices[0].message.content
    return punctuated_txt

In [4]:
# Define function to add full names of healthcare acronyms
def transcript_assistant(punctuated_txt):
    response = client.chat.completions.create(
        model="gpt-4",
        temperature=0,
        messages=[
            {
                "role": "system", 
                "content": "You are an intelligent assistant specializing in rewriting healthcare transcripts between doctors and patients. " 
                + "Your task is to process transcripts text of a patient interaction, ensuring that all healthcare terms are in the correct format. "
                + "For each term or acronym that is typically abbreviated as an acronym, the full term should be spelled out followed by the acronym in parentheses. "
                + "For example, 'EKG' should be transformed to 'Electrocardiogram (EKG/ECG)'. "
                + "Similarly, transform spoken numbers such as administered amounts or dosages into their numeric representations, followed by the correct measurement. "
                + "Once transcript is completed, produce the list of changes you made in a changelog section at the end of the transcript."
            },
            {
                "role": "user", 
                "content": punctuated_txt  
            }
        ]
    )

    transcript_txt = response.choices[0].message.content
    return transcript_txt

print(transcript_assistant(punctuation_assistant(txt)))

This one, they just handed me the Electrocardiogram (EKG/ECG) from triage, and it looks like they're having a heart attack. Hi there, I'm Dr. Beggars. This is Jake, my assistant. What it looks like on your Electrocardiogram (EKG/ECG), you might be having a heart attack, so we're going to be doing a lot of stuff really quickly, but we're going to have to get you to the catheterization laboratory (cath lab). Nurse, can you go ahead and give me an intravenous (IV), oxygen (O2) monitor? Let's get a cardiac workup, triage protocol. We're going to need a Complete Blood Count (CBC), a Basic Metabolic Panel (BMP), a troponin, a chest x-ray. Have you had any recent bleeding or clotting disorders, any history of gastrointestinal (GI) bleed or anything like that? Okay, so we'll go ahead and get a heparin bolus, heparin drip. That's going to be the myocardial infarction (MI) protocol for that, and a nitroglycerin (nitro) drip going as well, and some aspirin for baby aspirin. Can you tell me when y